In [1]:
import numpy as np
import pandas as pd
import folium

from src.dbtool import get_eved_db
from folium.vector_layers import PolyLine, CircleMarker

In [2]:
def load_dead_reckon() -> pd.DataFrame:
    db = get_eved_db()
    return db.query_df("select signal_id, latitude, longitude, jerk from dead_reckon")

In [3]:
def fit_bounding_box(html_map, bb_list):
    if isinstance(bb_list, list):
        ll = np.array(bb_list)
    else:
        ll = bb_list

    min_lat, max_lat = ll[:, 0].min(), ll[:, 0].max()
    min_lon, max_lon = ll[:, 1].min(), ll[:, 1].max()
    html_map.fit_bounds([[min_lat, min_lon], [max_lat, max_lon]])
    return html_map

In [4]:
def create_map() -> folium.Map:
    html_map = folium.Map(prefer_canvas=True, tiles="cartodbpositron", max_zoom=21, control_scale=True)
    return html_map

In [5]:
def show_dots(html_map: folium.Map,
              trajectory: np.ndarray,
              color: str = "red",
              opacity: float = 1.0,
              radius: int = 1) -> folium.Map:
    for lat, lon in trajectory:
        CircleMarker(location=[lat, lon], 
                     radius=radius, 
                     color=color,
                     opacity=opacity,
                     fill=True, 
                     fill_color=color).add_to(html_map)
    return html_map

In [6]:
df = load_dead_reckon()

In [7]:
df.head()

signal_id   latitude  longitude      jerk
0          1  42.278189 -83.748035 -0.438442
1          2  42.278201 -83.748034 -0.394598
2          3  42.278306 -83.748029  0.407409
3          4  42.278318 -83.748028  0.267620
4          5  42.278385 -83.748025 -0.337088

In [8]:
df["jerk"].mean(), df["jerk"].std()

(np.float64(-0.05336111526367536), np.float64(174.96200256884586))

In [9]:
df["jerk"].min()

np.float64(-283988.4806846186)

In [10]:
break_jerk_df = df[df["jerk"] <= df["jerk"].mean() - 3 * df["jerk"].std()]

In [11]:
break_jerk_df.shape

(4599, 4)

In [12]:
m = create_map()
m = fit_bounding_box(m, break_jerk_df[["latitude", "longitude"]].to_numpy())
m = show_dots(m, break_jerk_df[["latitude", "longitude"]].to_numpy(), color="red", opacity=0.2)
m

In [13]:
boost_jerk_df = df[df["jerk"] >= df["jerk"].mean() + 2 * df["jerk"].std()]

In [14]:
m = create_map()
m = fit_bounding_box(m, boost_jerk_df[["latitude", "longitude"]].to_numpy())
m = show_dots(m, boost_jerk_df[["latitude", "longitude"]].to_numpy(), color="blue", opacity=0.2)
m

In [15]:
boost_jerk_df.shape

(7378, 4)